<font color="#CC3D3D"><p>
# [Competition] Building a `CatBoost` Model with `Pipeline`

####  전역변수 설정

In [21]:
CATBOOST_VERSION = 3.0
NFOLDS = 15
SEED = 0
NCOMP = 50
P = 0.05

In [22]:
%matplotlib inline
import warnings
warnings.filterwarnings("ignore")

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.pipeline import Pipeline, make_pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import FunctionTransformer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import PowerTransformer 
from sklearn.preprocessing import OrdinalEncoder, OneHotEncoder
from sklearn.feature_selection import SelectPercentile, SelectKBest
from sklearn.model_selection import train_test_split, KFold, cross_validate, ShuffleSplit
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.decomposition import PCA, TruncatedSVD
from sklearn.metrics import mean_squared_error
from sklearn import set_config
from catboost import CatBoostRegressor
import re
from sklearn.cluster import KMeans
import statsmodels.api as sm

In [23]:
X_train = pd.read_csv('X_train_candidate2_feature.csv',encoding='cp949')
y_train = pd.read_csv('y_train.csv', encoding='cp949').Salary

X_test = pd.read_csv('X_test_candidate2_feature.csv',encoding='cp949')
test_id = pd.read_csv('X_test.csv',encoding='cp949').ID

In [2]:
X_train.

NameError: name 'X_train' is not defined

In [25]:
X_test.shape

(11048, 252)

#### 유형별 피처 분리

In [1]:
X_train

NameError: name 'X_train' is not defined

In [10]:
for df in [X_train, X_test]:
    numeric_features = df.dtypes[df.dtypes != "object"].index.tolist()

    categorical_features = df.dtypes[df.dtypes == "object"].index.tolist()


binary_features = ['직무태그','근무지역','근무형태']
categorical_features = [x for x in categorical_features if x not in binary_features]
    

X_train = X_train[numeric_features+categorical_features+binary_features]  # 순서 주의!!!
X_test = X_test[numeric_features+categorical_features+binary_features]

#CatBoost의 cat_features 파라미터에 지정할 범주형 피처 위치
cat_index = [list(X_train.columns).index(c) for c in categorical_features]

In [27]:
# cat_plus = []
# for i in X_train.columns:
#     if X_train[i].nunique() == 2:
#         cat_plus.append(i)

In [28]:
# DF = X_train[cat_plus]

In [29]:
# for df in [DF]:
#     num = df.dtypes[df.dtypes != "object"].index.tolist()
#     cat = df.dtypes[df.dtypes == "object"].index.tolist()
    
# # num 이 2개값만 가지는 피처중 수치형 cat은 범주형

In [30]:
# for df in [X_train, X_test]:
#     numeric_features = df.dtypes[df.dtypes != "object"].index.tolist()
#     categorical_features = df.dtypes[df.dtypes == "object"].index.tolist()

# binary_features = ['직무태그','근무지역','근무형태']
# categorical_features = [x for x in categorical_features if x not in binary_features]
# numeric_features = [x for x in numeric_features if x not in num]
# for i in num:
#     categorical_features.append(i)

In [31]:
# X_train = X_train[numeric_features+categorical_features+binary_features]  # 순서 주의!!!
# X_test = X_test[numeric_features+categorical_features+binary_features]
# #CatBoost의 cat_features 파라미터에 지정할 범주형 피처 위치
# cat_index = [list(X_train.columns).index(c) for c in categorical_features]

####  전처리 파이프라인 구축

In [32]:
# 상하한값 제한을 통한 결측값 처리 함수: FunctionTransformer를 통해 호출
def remove_outlier(X, q=0.05):  
    df = pd.DataFrame(X)
    return df.apply(lambda x: x.clip(x.quantile(q), x.quantile(1-q)), axis=0).values

# 회귀분석의 계수검정을 이용한 피처선택 전처리기 클래스
class MyFeatureSelector(TransformerMixin, BaseEstimator):
    # 전처리기 생성 즉, MyFeatureSelector() 호출시 실행
    def __init__(self, p=0.01):
        self.p = p

    # 전처리기의 fit() 호출시 실행
    def fit(self, X, y=None):
        X = sm.add_constant(X)
        results = sm.OLS(y, X).fit()
        self.cols = list(results.pvalues[1:] <= self.p)
        return self
    
    # 전처리기의 transform() 호출시 실행
    def transform(self, X):
        return X[:,self.cols].astype(np.int64)        
    
numeric_transformer = Pipeline(
    steps=[
        ("imputer", SimpleImputer(strategy="mean")),
        ("outlier", FunctionTransformer(remove_outlier, kw_args={'q':0.05})),
    ]
)

categorical_transformer = Pipeline(
    steps=[
        ("imputer", SimpleImputer(strategy="most_frequent")), 
        ("encoder", OrdinalEncoder(handle_unknown='use_encoded_value', unknown_value=99999, dtype=np.object)),
    ]
)

binary_transformer = Pipeline(
    steps=[
        ("impuer", FunctionTransformer(lambda x: x.fillna('없음'))),      
        ("corpus", FunctionTransformer(lambda x: x.str.replace('·',',').str.split(',').str.join(" "))),
        ("BoW", CountVectorizer()),
        ("dense", FunctionTransformer(lambda x: x.toarray().astype(int), accept_sparse=True)),
    ]
)

column_transformer = ColumnTransformer(
    transformers=[
        ("num", numeric_transformer, numeric_features),
        ("cat", categorical_transformer, categorical_features),
        ("bin1", make_pipeline(binary_transformer, TruncatedSVD(n_components=NCOMP,random_state=SEED)), binary_features[0]),
        ("bin2", make_pipeline(binary_transformer, MyFeatureSelector(p=P)), binary_features[1]),
        ("bin3", make_pipeline(binary_transformer, MyFeatureSelector(p=P)), binary_features[2]),
    ]
)

preprocessor = Pipeline(
    steps=[
        ("column", column_transformer), 
    ]
)

set_config(display="diagram")
preprocessor

Pipeline(steps=[('column',
                 ColumnTransformer(transformers=[('num',
                                                  Pipeline(steps=[('imputer',
                                                                   SimpleImputer()),
                                                                  ('outlier',
                                                                   FunctionTransformer(func=<function remove_outlier at 0x00000243A4540040>,
                                                                                       kw_args={'q': 0.05}))]),
                                                  ['근무경력', '대학성적', '직무태그글자수범위별',
                                                   '큰손', '직무태그_직무수', '직종수',
                                                   '세부직종수', '근무경력_x_대학성적',
                                                   '출신대학*대학성적',
                                                   '직무태그_직무수 + 근무경력_x',
                                                   '세부직종별 근무경력mean',
                                                   '세부직종별 근무경력median',
                                                   '...
                                                                   Pipeline(steps=[('impuer',
                                                                                    FunctionTransformer(func=<function <lambda> at 0x00000243A45400D0>)),
                                                                                   ('corpus',
                                                                                    FunctionTransformer(func=<function <lambda> at 0x00000243A41FBA60>)),
                                                                                   ('BoW',
                                                                                    CountVectorizer()),
                                                                                   ('dense',
                                                                                    FunctionTransformer(accept_sparse=True,
                                                                                                        func=<function <lambda> at 0x00000243A41FBAF0>))])),
                                                                  ('myfeatureselector',
                                                                   MyFeatureSelector(p=0.05))]),
                                                  '근무형태')]))])

####  데이터 전처리

In [33]:
X_train = preprocessor.fit_transform(X_train, y_train)
X_test = preprocessor.transform(X_test)

In [34]:
X = pd.DataFrame(X_train)
Y = pd.DataFrame(y_train)
Xt = pd.DataFrame(X_test)

In [35]:
kmeans = KMeans(n_clusters=5, init='k-means++')
kmeans.fit_transform(X,Y)
kmeans.transform(Xt)

pre_X5 = kmeans.predict(X)
k_means_5 = pd.DataFrame(pre_X5)
X['cluster5'] = k_means_5 

pre_Xt5 = kmeans.predict(Xt)
k_means_t5 = pd.DataFrame(pre_Xt5)
Xt['cluster5'] = k_means_t5 

In [36]:
kmeans10 = KMeans(n_clusters=10, init='k-means++')
kmeans10.fit_transform(X,Y)
kmeans10.transform(Xt)

pre_X10 = kmeans10.predict(X)
k_means_10 = pd.DataFrame(pre_X10)
X['cluster10'] = k_means_10 

pre_Xt10 = kmeans10.predict(Xt)
k_means_t10 = pd.DataFrame(pre_Xt10)
Xt['cluster10'] = k_means_t10 

In [37]:
kmeans15 = KMeans(n_clusters=15, init='k-means++')
kmeans15.fit_transform(X,Y)
kmeans15.transform(Xt)

pre_X15 = kmeans15.predict(X)
k_means_15 = pd.DataFrame(pre_X15)
X['cluster15'] = k_means_15 

pre_Xt15 = kmeans15.predict(Xt)
k_means_t15 = pd.DataFrame(pre_Xt15)
Xt['cluster15'] = k_means_t15 

In [38]:
X_train = np.array(X)
X_test = np.array(Xt)
y_train = np.array(Y)

#### 모형 생성

In [39]:
%%time

# 최적화된 하이퍼파라미터로 OOF를 수행하여 최종 CatBoost 모형 생성:
# No tuning => tuning한 모델에 비해 성능이 떨어지지 않음

#sscv = ShuffleSplit(test_size=.3334, n_splits=5, random_state=0)
models = cross_validate(CatBoostRegressor(task_type = 'CPU',learning_rate=0.03,iterations=7000,cat_features=cat_index, verbose=True, random_state=SEED),
                        X_train, y_train, 
                        cv=NFOLDS, 
                        scoring='neg_mean_squared_error', 
                        return_estimator=True)
oof_pred = np.array([m.predict(X_test) for m in models['estimator']]).mean(axis=0)

scores = models['test_score']
print("\nCatBoost CV scores: ", np.sqrt(-1*scores))
print("CatBoost CV mean = %.2f" % np.sqrt(-1*scores.mean()), "with std = %.2f" % np.sqrt(scores.std()))

0:	learn: 1226.6590672	total: 300ms	remaining: 34m 56s
1:	learn: 1211.1394649	total: 466ms	remaining: 27m 10s
2:	learn: 1196.5548830	total: 600ms	remaining: 23m 18s
3:	learn: 1182.1719500	total: 734ms	remaining: 21m 23s
4:	learn: 1167.2408459	total: 865ms	remaining: 20m 9s
5:	learn: 1153.5037518	total: 966ms	remaining: 18m 45s
6:	learn: 1140.3136156	total: 1.08s	remaining: 17m 55s
7:	learn: 1127.9974923	total: 1.18s	remaining: 17m 14s
8:	learn: 1116.7292286	total: 1.28s	remaining: 16m 34s
9:	learn: 1105.4180736	total: 1.38s	remaining: 16m 2s
10:	learn: 1094.7886359	total: 1.47s	remaining: 15m 33s
11:	learn: 1084.3868326	total: 1.58s	remaining: 15m 20s
12:	learn: 1074.8953560	total: 1.69s	remaining: 15m 8s
13:	learn: 1065.6547565	total: 1.78s	remaining: 14m 48s
14:	learn: 1056.4279847	total: 1.87s	remaining: 14m 32s
15:	learn: 1047.7732542	total: 1.97s	remaining: 14m 21s
16:	learn: 1039.5295845	total: 2.07s	remaining: 14m 10s
17:	learn: 1031.8561765	total: 2.17s	remaining: 14m 1s
18:	le

150:	learn: 825.3678184	total: 15.5s	remaining: 11m 42s
151:	learn: 825.0657592	total: 15.6s	remaining: 11m 43s
152:	learn: 824.8530995	total: 15.7s	remaining: 11m 42s
153:	learn: 824.5929376	total: 15.8s	remaining: 11m 44s
154:	learn: 824.2675502	total: 15.9s	remaining: 11m 44s
155:	learn: 824.0107520	total: 16s	remaining: 11m 43s
156:	learn: 823.9893137	total: 16.1s	remaining: 11m 43s
157:	learn: 823.6504192	total: 16.2s	remaining: 11m 42s
158:	learn: 823.2735959	total: 16.3s	remaining: 11m 42s
159:	learn: 822.9352562	total: 16.4s	remaining: 11m 41s
160:	learn: 822.6499525	total: 16.5s	remaining: 11m 41s
161:	learn: 822.6487390	total: 16.5s	remaining: 11m 38s
162:	learn: 822.4648596	total: 16.6s	remaining: 11m 37s
163:	learn: 822.4567278	total: 16.7s	remaining: 11m 35s
164:	learn: 822.2230063	total: 16.8s	remaining: 11m 34s
165:	learn: 821.8705263	total: 16.9s	remaining: 11m 34s
166:	learn: 821.7073944	total: 17s	remaining: 11m 33s
167:	learn: 821.7029159	total: 17s	remaining: 11m 32

298:	learn: 800.4774852	total: 29s	remaining: 10m 50s
299:	learn: 800.3167545	total: 29.1s	remaining: 10m 50s
300:	learn: 800.3147982	total: 29.2s	remaining: 10m 49s
301:	learn: 800.1202433	total: 29.3s	remaining: 10m 49s
302:	learn: 800.1195962	total: 29.3s	remaining: 10m 47s
303:	learn: 799.9831138	total: 29.4s	remaining: 10m 47s
304:	learn: 799.7666797	total: 29.5s	remaining: 10m 47s
305:	learn: 799.3423515	total: 29.6s	remaining: 10m 47s
306:	learn: 799.1183434	total: 29.7s	remaining: 10m 46s
307:	learn: 798.9884582	total: 29.8s	remaining: 10m 46s
308:	learn: 798.8687841	total: 29.9s	remaining: 10m 46s
309:	learn: 798.6050519	total: 30s	remaining: 10m 46s
310:	learn: 798.4603536	total: 30s	remaining: 10m 46s
311:	learn: 798.3976512	total: 30.1s	remaining: 10m 45s
312:	learn: 798.2434458	total: 30.2s	remaining: 10m 45s
313:	learn: 798.0904992	total: 30.3s	remaining: 10m 45s
314:	learn: 798.0878622	total: 30.4s	remaining: 10m 45s
315:	learn: 797.8640346	total: 30.5s	remaining: 10m 45

447:	learn: 783.7816861	total: 42.8s	remaining: 10m 25s
448:	learn: 783.7723850	total: 42.9s	remaining: 10m 25s
449:	learn: 783.7614219	total: 42.9s	remaining: 10m 25s
450:	learn: 783.7541640	total: 43s	remaining: 10m 24s
451:	learn: 783.6352242	total: 43.1s	remaining: 10m 24s
452:	learn: 783.6265476	total: 43.2s	remaining: 10m 24s
453:	learn: 783.6183795	total: 43.3s	remaining: 10m 24s
454:	learn: 783.3825368	total: 43.4s	remaining: 10m 24s
455:	learn: 783.2324250	total: 43.5s	remaining: 10m 24s
456:	learn: 782.9607838	total: 43.6s	remaining: 10m 24s
457:	learn: 782.8797924	total: 43.7s	remaining: 10m 24s
458:	learn: 782.8718913	total: 43.8s	remaining: 10m 24s
459:	learn: 782.7221018	total: 43.9s	remaining: 10m 24s
460:	learn: 782.6563464	total: 44s	remaining: 10m 24s
461:	learn: 782.6477511	total: 44.1s	remaining: 10m 24s
462:	learn: 782.4148840	total: 44.2s	remaining: 10m 24s
463:	learn: 782.2759803	total: 44.4s	remaining: 10m 25s
464:	learn: 782.2322849	total: 44.5s	remaining: 10m 

595:	learn: 766.0922607	total: 57.3s	remaining: 10m 16s
596:	learn: 766.0014091	total: 57.4s	remaining: 10m 16s
597:	learn: 765.9354479	total: 57.5s	remaining: 10m 15s
598:	learn: 765.8101436	total: 57.6s	remaining: 10m 15s
599:	learn: 765.7019208	total: 57.7s	remaining: 10m 15s
600:	learn: 765.4710122	total: 57.8s	remaining: 10m 15s
601:	learn: 765.4152127	total: 57.9s	remaining: 10m 15s
602:	learn: 765.2964887	total: 58s	remaining: 10m 15s
603:	learn: 765.1940201	total: 58.1s	remaining: 10m 15s
604:	learn: 765.0575616	total: 58.2s	remaining: 10m 15s
605:	learn: 764.9960070	total: 58.3s	remaining: 10m 15s
606:	learn: 764.9913971	total: 58.4s	remaining: 10m 15s
607:	learn: 764.9068649	total: 58.5s	remaining: 10m 15s
608:	learn: 764.7043385	total: 58.6s	remaining: 10m 14s
609:	learn: 764.6485117	total: 58.7s	remaining: 10m 15s
610:	learn: 764.4867201	total: 58.8s	remaining: 10m 14s
611:	learn: 764.3534887	total: 58.9s	remaining: 10m 14s
612:	learn: 764.2096189	total: 59s	remaining: 10m 

...

6332:	learn: 467.0166547	total: 10m 36s	remaining: 1m 6s
6333:	learn: 466.9843186	total: 10m 36s	remaining: 1m 6s
6334:	learn: 466.9503719	total: 10m 36s	remaining: 1m 6s
6335:	learn: 466.9310487	total: 10m 36s	remaining: 1m 6s
6336:	learn: 466.8946540	total: 10m 36s	remaining: 1m 6s
6337:	learn: 466.8695634	total: 10m 36s	remaining: 1m 6s
6338:	learn: 466.8496480	total: 10m 36s	remaining: 1m 6s
6339:	learn: 466.8141011	total: 10m 36s	remaining: 1m 6s
6340:	learn: 466.7907955	total: 10m 36s	remaining: 1m 6s
6341:	learn: 466.7523316	total: 10m 36s	remaining: 1m 6s
6342:	learn: 466.7403732	total: 10m 37s	remaining: 1m 5s
6343:	learn: 466.6890578	total: 10m 37s	remaining: 1m 5s
6344:	learn: 466.6884116	total: 10m 37s	remaining: 1m 5s
6345:	learn: 466.6539848	total: 10m 37s	remaining: 1m 5s
6346:	learn: 466.6376301	total: 10m 37s	remaining: 1m 5s
6347:	learn: 466.6100434	total: 10m 37s	remaining: 1m 5s
6348:	learn: 466.5742806	total: 10m 37s	remaining: 1m 5s
6349:	learn: 466.5323796	total:

6477:	learn: 462.8052392	total: 10m 51s	remaining: 52.5s
6478:	learn: 462.7970906	total: 10m 51s	remaining: 52.4s
6479:	learn: 462.7865654	total: 10m 51s	remaining: 52.3s
6480:	learn: 462.7742888	total: 10m 51s	remaining: 52.2s
6481:	learn: 462.7283036	total: 10m 51s	remaining: 52.1s
6482:	learn: 462.6553499	total: 10m 52s	remaining: 52s
6483:	learn: 462.6481799	total: 10m 52s	remaining: 51.9s
6484:	learn: 462.5865447	total: 10m 52s	remaining: 51.8s
6485:	learn: 462.5454838	total: 10m 52s	remaining: 51.7s
6486:	learn: 462.5384850	total: 10m 52s	remaining: 51.6s
6487:	learn: 462.5243337	total: 10m 52s	remaining: 51.5s
6488:	learn: 462.5129615	total: 10m 52s	remaining: 51.4s
6489:	learn: 462.5117235	total: 10m 52s	remaining: 51.3s
6490:	learn: 462.4887927	total: 10m 52s	remaining: 51.2s
6491:	learn: 462.4601596	total: 10m 52s	remaining: 51.1s
6492:	learn: 462.4120337	total: 10m 53s	remaining: 51s
6493:	learn: 462.3886436	total: 10m 53s	remaining: 50.9s
6494:	learn: 462.3165911	total: 10m

6623:	learn: 458.4733159	total: 11m 7s	remaining: 37.9s
6624:	learn: 458.4412755	total: 11m 7s	remaining: 37.8s
6625:	learn: 458.3818923	total: 11m 7s	remaining: 37.7s
6626:	learn: 458.3514989	total: 11m 7s	remaining: 37.6s
6627:	learn: 458.3256062	total: 11m 7s	remaining: 37.5s
6628:	learn: 458.2964897	total: 11m 7s	remaining: 37.4s
6629:	learn: 458.2629542	total: 11m 7s	remaining: 37.3s
6630:	learn: 458.2510089	total: 11m 7s	remaining: 37.2s
6631:	learn: 458.2503953	total: 11m 8s	remaining: 37.1s
6632:	learn: 458.1983244	total: 11m 8s	remaining: 37s
6633:	learn: 458.1922464	total: 11m 8s	remaining: 36.9s
6634:	learn: 458.1734322	total: 11m 8s	remaining: 36.8s
6635:	learn: 458.1672826	total: 11m 8s	remaining: 36.7s
6636:	learn: 458.1466259	total: 11m 8s	remaining: 36.6s
6637:	learn: 458.1210181	total: 11m 8s	remaining: 36.5s
6638:	learn: 458.1014546	total: 11m 8s	remaining: 36.4s
6639:	learn: 458.0625155	total: 11m 8s	remaining: 36.3s
6640:	learn: 458.0324208	total: 11m 9s	remaining: 

6768:	learn: 454.4915611	total: 11m 22s	remaining: 23.3s
6769:	learn: 454.4665434	total: 11m 22s	remaining: 23.2s
6770:	learn: 454.4455299	total: 11m 22s	remaining: 23.1s
6771:	learn: 454.3573598	total: 11m 22s	remaining: 23s
6772:	learn: 454.3258043	total: 11m 22s	remaining: 22.9s
6773:	learn: 454.2932422	total: 11m 22s	remaining: 22.8s
6774:	learn: 454.2768549	total: 11m 22s	remaining: 22.7s
6775:	learn: 454.2548478	total: 11m 23s	remaining: 22.6s
6776:	learn: 454.1998702	total: 11m 23s	remaining: 22.5s
6777:	learn: 454.1712984	total: 11m 23s	remaining: 22.4s
6778:	learn: 454.1481264	total: 11m 23s	remaining: 22.3s
6779:	learn: 454.1208693	total: 11m 23s	remaining: 22.2s
6780:	learn: 454.1141174	total: 11m 23s	remaining: 22.1s
6781:	learn: 454.0787189	total: 11m 23s	remaining: 22s
6782:	learn: 454.0188302	total: 11m 23s	remaining: 21.9s
6783:	learn: 453.9935850	total: 11m 23s	remaining: 21.8s
6784:	learn: 453.9502111	total: 11m 24s	remaining: 21.7s
6785:	learn: 453.9157274	total: 11m

6913:	learn: 450.3224876	total: 11m 37s	remaining: 8.68s
6914:	learn: 450.3075592	total: 11m 37s	remaining: 8.57s
6915:	learn: 450.2524736	total: 11m 37s	remaining: 8.47s
6916:	learn: 450.2047822	total: 11m 37s	remaining: 8.37s
6917:	learn: 450.1844064	total: 11m 37s	remaining: 8.27s
6918:	learn: 450.1410991	total: 11m 38s	remaining: 8.17s
6919:	learn: 450.1131458	total: 11m 38s	remaining: 8.07s
6920:	learn: 450.0730236	total: 11m 38s	remaining: 7.97s
6921:	learn: 450.0422484	total: 11m 38s	remaining: 7.87s
6922:	learn: 450.0138480	total: 11m 38s	remaining: 7.77s
6923:	learn: 449.9794362	total: 11m 38s	remaining: 7.67s
6924:	learn: 449.9369372	total: 11m 38s	remaining: 7.57s
6925:	learn: 449.9095765	total: 11m 38s	remaining: 7.47s
6926:	learn: 449.8949962	total: 11m 39s	remaining: 7.37s
6927:	learn: 449.8707083	total: 11m 39s	remaining: 7.26s
6928:	learn: 449.8473525	total: 11m 39s	remaining: 7.17s
6929:	learn: 449.8268476	total: 11m 39s	remaining: 7.06s
6930:	learn: 449.7976211	total:

In [40]:
# submission 화일 생성
filename = f'catboost_799에iter추가직무태그띄워쓰기뺌_{np.sqrt(-1*scores.mean()):.2f}.csv'
pd.DataFrame({'ID':test_id, 'Salary':oof_pred}).to_csv(filename, index=False)

<font color="#CC3D3D"><p>
# End